In [1]:
import csv, sys
import io, textwrap, itertools
from Bio import SeqIO
from Bio.Seq import Seq
from Bio.SeqRecord import SeqRecord
csv.field_size_limit(sys.maxsize)
common_amino_acid_set = set(['R', 'X', 'S', 'G', 'W', 'I', 'Q', 'A', 'T', 'V', 'K', 'Y', 'C', 'N', 'L', 'F', 'D', 'M', 'P', 'H', 'E'])


def clean_seq(protein_id, seq):
    seq = seq.upper()
    new_seq = ""
    has_invalid_char = False
    invalid_char_set = set()
    for ch in seq:
        if 'A' <= ch <= 'Z' and ch not in ['J']:
            new_seq += ch
        else:
            invalid_char_set.add(ch)
            has_invalid_char = True
    if has_invalid_char:
        print("id: %s. Seq: %s" % (protein_id, seq))
        print("invalid char set:", invalid_char_set)
    return new_seq


def file_reader(filename, header=True, header_filter=True):
    if filename.endswith(".fa") or filename.endswith(".fas") or filename.endswith(".fasta"):
        return fasta_reader(filename)
    elif filename.endswith(".csv"):
        return csv_reader(filename, header=True, header_filter=True)
    elif filename.endswith(".tsv"):
        return tsv_reader(filename, header=True, header_filter=True)
    else:
        return txt_reader(filename, header=header, header_filter=header_filter)


def txt_reader(handle, header=True, header_filter=True):
    '''
    csv 读取器，适合大文件
    :param handle:
    :param header:
    :param header_filter: 返回结果是否去掉头
    :return:
    '''
    handle = handle if isinstance(handle, io.TextIOWrapper) else open(handle, 'r')
    try:
        cnt = 0
        for line in handle:
            cnt += 1
            if header and header_filter and cnt == 1:
                continue
            yield line.strip()
    except Exception as e:
        raise StopIteration
    finally:
        if not handle.closed:
            handle.close()


def tsv_reader(handle, header=True, header_filter=True):
    '''
    csv 读取器，适合大文件
    :param handle:
    :param header:
    :param header_filter: 返回结果是否去掉头
    :return:
    '''
    handle = handle if isinstance(handle, io.TextIOWrapper) else open(handle, 'r')
    try:
        reader = csv.reader(handle, delimiter="\t")
        cnt = 0
        for row in reader:
            cnt += 1
            if header and header_filter and cnt == 1:
                continue
            yield row
    except Exception as e:
        raise StopIteration
    finally:
        if not handle.closed:
            handle.close()


def csv_reader(handle, header=True, header_filter=True):
    '''
    csv 读取器，适合大文件
    :param handle:
    :param header:
    :param header_filter: 返回结果是否去掉头
    :return:
    '''
    handle = handle if isinstance(handle, io.TextIOWrapper) else open(handle, 'r')
    try:
        # data = csv.reader((line.replace('\0','') for line in data_initial), delimiter=",")
        # reader = csv.reader(handle)
        reader = csv.reader((line.replace('\0', '') for line in handle))
        cnt = 0
        for row in reader:
            cnt += 1
            if header and header_filter and cnt == 1:
                continue
            yield row
    except Exception as e:
        raise StopIteration
    finally:
        if not handle.closed:
            handle.close()


def txt_writer(dataset, handle, header=None):
    '''
    txt 写
    :param dataset: 数据
    :param handle: 文件
    :param header: 头
    :return:
    '''
    with open(handle, "w") as wfp:
        if header:
            if isinstance(header, list):
                wfp.write(",".join(header) + "\n")
            else:
                wfp.write(header + "\n")
        for row in dataset:
            wfp.write(str(row) + "\n")


def csv_writer(dataset, handle, header):
    '''
    csv 写，适合大文件
    :param dataset: 数据
    :param handle: 文件
    :param header: 头
    :return:
    '''
    handle = handle if isinstance(handle, io.TextIOWrapper) else open(handle, 'w')
    try:
        writer = csv.writer(handle)
        if header:
            writer.writerow(header)
        for row in dataset:
            writer.writerow(row)
    except Exception as e:
        raise e
    finally:
        if not handle.closed:
            handle.close()


def fasta_reader(handle, width=None):
    """
    Reads a FASTA file, yielding header, sequence pairs for each sequence recovered 适合大文件
    args:
        :handle (str, pathliob.Path, or file pointer) - fasta to read from
        :width (int or None) - formats the sequence to have max `width` character per line.
                               If <= 0, processed as None. If None, there is no max width.
    yields:
        :(header, sequence) tuples
    returns:
        :None
    """
    FASTA_STOP_CODON = "*"

    handle = handle if isinstance(handle, io.TextIOWrapper) else open(handle, 'r')
    width = width if isinstance(width, int) and width > 0 else None
    try:
        header = None
        for is_header, group in itertools.groupby(handle, lambda line: line.startswith(">")):
            if is_header:
                header = group.__next__().strip()
            else:
                seq = ''.join(line.strip() for line in group).strip().rstrip(FASTA_STOP_CODON)
                if width is not None:
                    seq = textwrap.fill(seq, width)
                yield header, seq
    except Exception as e:
        raise StopIteration
    finally:
        if not handle.closed:
            handle.close()


def write_fasta(filepath, sequences):
    '''
    write fasta file
    :param filepath: savepath
    :param sequences: fasta sequence(each item: [id, seq])
    :return:
    '''

    if sequences:
        with open(filepath, "w") as output_handle:
            if len(sequences[0]) > 1 and isinstance(sequences[0][0], str):
                for row in sequences:
                    protein_id = row[0]
                    seq = row[1]
                    sequence = SeqRecord(Seq(seq, None), id=protein_id[1:] if protein_id and protein_id[0] == ">" else protein_id, description="")
                    SeqIO.write(sequence, output_handle, "fasta")
            else:
                for sequence in sequences:
                    SeqIO.write(sequence, output_handle, "fasta")


In [2]:
# blast
unchecked_blast = "../results/Blastp/blastp_init.ids.labels"
unchecked_blast_info = []
unchecked_blast_set = set()
checked_blast = "../results/Blastp/blastp_verified.ids.labels"
checked_blast_info = []
checked_blast_set = set()
for row in tsv_reader(unchecked_blast, header=True, header_filter=True):
    seq_id = row[0]
    if seq_id[0] == ">":
        seq_id = seq_id[1:]
    unchecked_blast_info.append([seq_id, row[1]])
    unchecked_blast_set.add(seq_id)
print(len(unchecked_blast_info))
print(len(unchecked_blast_set))
for row in tsv_reader(checked_blast, header=True, header_filter=True):
    seq_id = row[0]
    if seq_id[0] == ">":
        seq_id = seq_id[1:]
    checked_blast_info.append([seq_id, row[1]])
    checked_blast_set.add(seq_id)
print(len(checked_blast_info))
print(len(checked_blast_set))


1025076
1025076
692206
692206


In [3]:
# kofamscan
unchecked_kofamscan = "../results/KofamScan/kofamscan_init.ids.labels"
unchecked_kofamscan_info = []
unchecked_kofamscan_set = set()
unchecked_kofamscan_repeat = {}
checked_kofamscan = "../results/KofamScan/kofamscan_verified.ids.labels"
checked_kofamscan_info = []
checked_kofamscan_set = set()
for row in tsv_reader(unchecked_kofamscan, header=True, header_filter=True):
    seq_id = row[0]
    if seq_id[0] == ">":
        seq_id = seq_id[1:]
    unchecked_kofamscan_info.append([seq_id, row[1]])
    if seq_id in unchecked_kofamscan_set:
        if seq_id not in unchecked_kofamscan_repeat:
            unchecked_kofamscan_repeat[seq_id] = 1
        else:
            unchecked_kofamscan_repeat[seq_id] += 1
    else:
        unchecked_kofamscan_set.add(seq_id)
print(len(unchecked_kofamscan_info))
print(len(unchecked_kofamscan_set))
for row in tsv_reader(checked_kofamscan, header=True, header_filter=True):
    seq_id = row[0]
    if seq_id[0] == ">":
        seq_id = seq_id[1:]
    checked_kofamscan_info.append([seq_id, row[1]])
    checked_kofamscan_set.add(seq_id)
print(len(checked_kofamscan_info))
print(len(checked_kofamscan_set))
print(len(unchecked_kofamscan_repeat))


2603796
2586059
2364031
2364026
17690


In [4]:
# lucapcycle
unchecked_lucapcycle = "../results/LucaPCycle/lucapcycle_init.csv"
unchecked_lucapcycle_info = []
unchecked_lucapcycle_set = set()
checked_lucapcycle = "../results/LucaPCycle/lucapcycle_verified.ids.labels"
checked_lucapcycle_info = []
checked_lucapcycle_set = set()
unable_checked_lucapcycle = "../results/LucaPCycle/lucapcycle_unverifiable.ids"
unable_checked_lucapcycle_info = []
unable_checked_lucapcycle_set = set()
for row in csv_reader(unchecked_lucapcycle, header=True, header_filter=True):
    seq_id = row[0]
    if seq_id[0] == ">":
        seq_id = seq_id[1:]
    unchecked_lucapcycle_info.append([seq_id, row[1]])
    unchecked_lucapcycle_set.add(seq_id)
print(len(unchecked_lucapcycle_info))
print(len(unchecked_lucapcycle_set))
for row in tsv_reader(checked_lucapcycle, header=True, header_filter=True):
    seq_id = row[0]
    if seq_id[0] == ">":
        seq_id = seq_id[1:]
    checked_lucapcycle_info.append([seq_id, row[1]])
    checked_lucapcycle_set.add(seq_id)
print(len(checked_lucapcycle_info))
print(len(checked_lucapcycle_set))
for row in tsv_reader(unable_checked_lucapcycle, header=True, header_filter=True):
    seq_id = row[0]
    if seq_id[0] == ">":
        seq_id = seq_id[1:]
    unable_checked_lucapcycle_info.append(seq_id)
    unable_checked_lucapcycle_set.add(seq_id)
print(len(unable_checked_lucapcycle_info))
print(len(unable_checked_lucapcycle_set))


1481237
1481237
1347010
1347010
134227
134227


In [5]:
unchecked_blast_fasta = []
checked_blast_fasta = []

unchecked_kofamscan_fasta = []
checked_kofamscan_fasta = []

unchecked_kofamscan_repeat_fasta = []

unchecked_lucapcycle_fasta = []
checked_lucapcycle_fasta = []
unable_checked_lucapcycle_fasta = []

filepaths = ["../inference_data/dRep95_QS50_bins_all_gene.faa", "../inference_data/non-redundant_genes_renamed.faa"]
total_seqs = 0
for filepath in filepaths:
    for row in fasta_reader(filepath):
        seq_id = row[0]
        seq = row[1].strip().upper()
        total_seqs += 1
        if seq_id[0] == ">":
            seq_id = seq_id[1:]
        if seq_id in unchecked_blast_set:
            unchecked_blast_fasta.append([seq_id, seq])
        if seq_id in checked_blast_set:
            checked_blast_fasta.append([seq_id, seq])
        if seq_id in unchecked_kofamscan_set:
            unchecked_kofamscan_fasta.append([seq_id, seq])
        if seq_id in checked_kofamscan_set:
            checked_kofamscan_fasta.append([seq_id, seq])
        if seq_id in unchecked_lucapcycle_set:
            unchecked_lucapcycle_fasta.append([seq_id, seq])
        if seq_id in checked_lucapcycle_set:
            checked_lucapcycle_fasta.append([seq_id, seq])
        if seq_id in unable_checked_lucapcycle_set:
            unable_checked_lucapcycle_fasta.append([seq_id, seq])
        if seq_id in unchecked_kofamscan_repeat:
            for _ in range(unchecked_kofamscan_repeat[seq_id]):
                unchecked_kofamscan_repeat_fasta.append([seq_id, seq])
unchecked_kofamscan_fasta = unchecked_kofamscan_fasta + unchecked_kofamscan_repeat_fasta

In [6]:
print("total_seqs: %d" % total_seqs)   
print(len(unchecked_blast_fasta))
print(len(checked_blast_fasta))
print(len(unchecked_kofamscan_repeat_fasta))
print(len(unchecked_kofamscan_fasta))
print(len(checked_kofamscan_fasta))
print(len(unchecked_lucapcycle_fasta))
print(len(checked_lucapcycle_fasta))
print(len(unable_checked_lucapcycle_fasta))

write_fasta("../results/Blastp/blastp_init.fasta", unchecked_blast_fasta)
write_fasta("../results/Blastp/blastp_verified.fasta", checked_blast_fasta)

write_fasta("../results/KofamScan/kofamscan_init.fasta", unchecked_kofamscan_fasta)
write_fasta("../results/KofamScan/kofamscan_verified.fasta", checked_kofamscan_fasta)


write_fasta("../results/LucaPCycle/lucapcycle_init.fasta", unchecked_lucapcycle_fasta)
write_fasta("../results/LucaPCycle/lucapcycle_verified.fasta", checked_lucapcycle_fasta)
write_fasta("../results/LucaPCycle/lucapcycle_unverifiable.fasta", unable_checked_lucapcycle_fasta)

total_seqs: 151187265
1025076
692206
17737
2603796
2364026
1481237
1347010
134227
